In [10]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [11]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [12]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/PhysicalProgressReport/YearWiseHouseCompletionReport.aspx?"
params = {
    'params': 0
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [13]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddlFinYear'
scheme_select_name = 'ctl00$ContentPlaceHolder1$ddlScheme'
state_select_name = 'ctl00$ContentPlaceHolder1$ddlState'
district_select_name = 'ctl00$ContentPlaceHolder1$ddlDistrict'
block_select_name = 'ctl00$ContentPlaceHolder1$ddlBlock'
submit_button_name = 'ctl00$ContentPlaceHolder1$btnSubmit'
content_table_pane = 'ContentPlaceHolder1_gvDataPanelItem'
content_table_head_id = 'ContentPlaceHolder1_gvDataCopy'
content_table_id = 'ContentPlaceHolder1_gvData'

In [14]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

#Check Submit button
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )

#Check table
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )    
    
#Check submit button
def delete_content():
    driver.execute_script("return document.getElementsByClassName('col-lg-10')[0].remove()")
def check_error():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.ID, "ContentPlaceHolder1_lbl_data_msg" ) ) )
    

In [15]:
def get_total_houselist():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
    WebDriverWait(driver, 2).until(element_present)
    #Once Loaded Create DataFrame from Table
    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
    df = pd.read_html(html_table, skiprows=0, header=0)[0]
    df = df[1:-1]        
    total_houses_completed = list(df[df.columns[-1]])
    return total_houses_completed

In [23]:
#Start Chrome
driver.get(url)

#Year Selection
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[6:7]
for year in yearlist:    
    print("--Scrapping data for Year: ", year['text'])
    year_query = ".//option[@value='" + year['value'] + "']"
    delete_submit()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    check_submit()
    
    #DataStore
    df_list = []
    
    #Scheme Selection
    schemelist = build_list(scheme_select_name)[30:]
    for scheme in schemelist:
        print("--//--Scrapping data for scheme: ", scheme['text'])
        scheme_query = ".//option[@value='" + scheme['value'] + "']"
        delete_submit()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, scheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        check_submit()
        
        # Delete Content
        delete_content()        
        #Submit button
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, submit_button_name))
        )
        element.click()
        
        #Load Filter List
        state_total_houses_completed = get_total_houselist();
        
        #state Selection
        statelist = build_list(state_select_name)
        for stateindex, state in enumerate(statelist):
            print("--//--//--Scrapping data for state: ", state['text'])
            if state_total_houses_completed[int(stateindex)] > 0:
                state_query = ".//option[@value='" + state['value'] + "']"
                delete_submit()
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, state_select_name))
                )
                element.find_element_by_xpath(state_query).click()
                check_submit()
                
                # Delete Content
                delete_content()        
                #Submit button
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                )
                element.click()

                #Load Filter List
                district_total_houses_completed = get_total_houselist();
         
                #district Selection
                districtlist = build_list(district_select_name)
                for districtindex, district in enumerate(districtlist):
                    print("--//--//--//--Scrapping data for district: ", district['text'])
                    if district_total_houses_completed[int(districtindex)] > 0:
                        district_query = ".//option[@value='" + district['value'] + "']"
                        delete_submit()
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, district_select_name))
                        )
                        element.find_element_by_xpath(district_query).click()
                        check_submit()
                        
                        # Delete Content
                        delete_content()        
                        #Submit button
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, submit_button_name))
                        )
                        element.click()

                        #Load Filter List
                        block_total_houses_completed = get_total_houselist();

                        #block Selection
                        blocklist = build_list(block_select_name)
                        for blockindex, block in enumerate(blocklist):
                            print("--//--//--//--//--Scrapping data for block: ", block['text'])
                            if block_total_houses_completed[int(blockindex)] > 0:
                                block_query = ".//option[@value='" + block['value'] + "']"
                                delete_submit()
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, block_select_name))
                                )
                                element.find_element_by_xpath(block_query).click()
                                check_submit()

                                # Delete Content
                                delete_content()

                                #Submit button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                                )
                                element.click()

                                try:
                                    #Wait for Table to Load fully
                                    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
                                    WebDriverWait(driver, 2).until(element_present)

                                    #Once Loaded Create DataFrame from Table
                                    #html_head = driver.find_element_by_id(content_table_head_id).get_attribute('outerHTML')
                                    #df = pd.read_html(html_head, skiprows=0)[0]
                                    #table_head = list(df.values[0])
                                    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
                                    df = pd.read_html(html_table, skiprows=0, header=0)[0]
                                    df = df[1:-1]
                                    #df.columns = table_head
                                    df['Financial Year'] = year['text']
                                    df['Scheme'] = scheme['text']
                                    df['State Name'] = state['text']
                                    df['District Name'] = district['text']
                                    df['Block Name'] = block['text']
                                    df_list.append(df)
                                except Exception as e:
                                    print("Error while table data |", e)


    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df = df.reset_index().drop(columns=['index', '#SNo'])
    df['#SNo'] = df.index + 1
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

--Scrapping data for Year:  2016-2017
--//--Scrapping data for scheme:  PRIMITIVE TRIBAL GROUP
--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--//--Scrapping data for district:  AGAR-MALWA
--//--//--//--Scrapping data for district:  ALIRAJPUR
--//--//--//--Scrapping data for district:  ANUPPUR
--//--//--//--Scrapping data for district:  ASHOK NAGAR
--//--//--//--Scrapping data for district:  BALAGHAT
--//--//--//--Scrapping data for district:  BARWANI
--//--//-

--//--//--//--//--Scrapping data for block:  बेगूँ
--//--//--//--//--Scrapping data for block:  भदेसर
--//--//--//--//--Scrapping data for block:  भूपालसागर
--//--//--//--//--Scrapping data for block:  भैसरोड़गढ
--//--//--//--//--Scrapping data for block:  राशमी
--//--//--//--Scrapping data for district:  CHURU
--//--//--//--Scrapping data for district:  DAUSA
--//--//--//--//--Scrapping data for block:  LAWAAN
--//--//--//--//--Scrapping data for block:  द‍ौसा
--//--//--//--//--Scrapping data for block:  बांदीकुई
--//--//--//--//--Scrapping data for block:  महवा
--//--//--//--//--Scrapping data for block:  लालसोट
--//--//--//--//--Scrapping data for block:  सिकराय
--//--//--//--Scrapping data for district:  DHOLPUR
--//--//--//--Scrapping data for district:  DUNGARPUR
--//--//--//--Scrapping data for district:  HANUMANGARH
--//--//--//--Scrapping data for district:  JAIPUR
--//--//--//--Scrapping data for district:  JAISALMER
--//--//--//--Scrapping data for district:  JALORE
--//--//

--//--//--//--//--Scrapping data for block:  SAFIDON
--//--//--//--//--Scrapping data for block:  UCHANA
--//--//--//--Scrapping data for district:  KAITHAL
--//--//--//--//--Scrapping data for block:  GUHLA
--//--//--//--//--Scrapping data for block:  KAITHAL
--//--//--//--//--Scrapping data for block:  KALAYAT
--//--//--//--//--Scrapping data for block:  PUNDRI
--//--//--//--//--Scrapping data for block:  RAJOUND
--//--//--//--//--Scrapping data for block:  SIWAN
--//--//--//--Scrapping data for district:  KARNAL
--//--//--//--//--Scrapping data for block:  ASSANDH
--//--//--//--//--Scrapping data for block:  GHARAUNDA (PART)
--//--//--//--//--Scrapping data for block:  INDRI
--//--//--//--//--Scrapping data for block:  KARNAL
--//--//--//--//--Scrapping data for block:  NILOKHERI
--//--//--//--//--Scrapping data for block:  NISSING AT CHIRAO
--//--//--//--Scrapping data for district:  KURUKSHETRA
--//--//--//--//--Scrapping data for block:  BABAIN
--//--//--//--//--Scrapping data fo

--//--//--//--Scrapping data for district:  KULLU
--//--//--//--//--Scrapping data for block:  ANNI
--//--//--//--//--Scrapping data for block:  BANJAR
--//--//--//--//--Scrapping data for block:  KULLU
--//--//--//--//--Scrapping data for block:  NAGAR
--//--//--//--//--Scrapping data for block:  NIRMAND
--//--//--//--Scrapping data for district:  LAHUL AND SPITI
--//--//--//--//--Scrapping data for block:  LAHAUL
--//--//--//--//--Scrapping data for block:  SPITI
--//--//--//--Scrapping data for district:  MANDI
--//--//--//--//--Scrapping data for block:  BALH
--//--//--//--//--Scrapping data for block:  CHAUNTRA
--//--//--//--//--Scrapping data for block:  DHARAMPUR
--//--//--//--//--Scrapping data for block:  DRANG
--//--//--//--//--Scrapping data for block:  GOHAR
--//--//--//--//--Scrapping data for block:  GOPALPUR
--//--//--//--//--Scrapping data for block:  KARSOG
--//--//--//--//--Scrapping data for block:  MANDI SADAR
--//--//--//--//--Scrapping data for block:  SERAJ
--//-

--//--//--//--//--Scrapping data for block:  MOHADI
--//--//--//--//--Scrapping data for block:  PAUNI
--//--//--//--//--Scrapping data for block:  SAKOLI
--//--//--//--//--Scrapping data for block:  TUMSAR
--//--//--//--Scrapping data for district:  BULDHANA
--//--//--//--//--Scrapping data for block:  BULDANA
--//--//--//--//--Scrapping data for block:  CHIKHLI
--//--//--//--//--Scrapping data for block:  DEULGAON RAJA
--//--//--//--//--Scrapping data for block:  JALGAON (JAMOD)
--//--//--//--//--Scrapping data for block:  KHAMGAON
--//--//--//--//--Scrapping data for block:  LONAR
--//--//--//--//--Scrapping data for block:  MALKAPUR
--//--//--//--//--Scrapping data for block:  MEHKAR
--//--//--//--//--Scrapping data for block:  MOTALA
--//--//--//--//--Scrapping data for block:  NANDURA
--//--//--//--//--Scrapping data for block:  SANGRAMPUR
--//--//--//--//--Scrapping data for block:  SHEGAON
--//--//--//--//--Scrapping data for block:  SINDKHED RAJA
--//--//--//--Scrapping data f

...

--//--//--//--//--Scrapping data for block:  PACHORA
--//--//--//--//--Scrapping data for block:  PAROLA
--//--//--//--//--Scrapping data for block:  RAVER
--//--//--//--//--Scrapping data for block:  YAWAL
--//--//--//--Scrapping data for district:  JALNA
--//--//--//--Scrapping data for district:  KOLHAPUR
--//--//--//--Scrapping data for district:  LATUR
--//--//--//--//--Scrapping data for block:  AHMADPUR
--//--//--//--//--Scrapping data for block:  AUSA
--//--//--//--//--Scrapping data for block:  CHAKUR
--//--//--//--//--Scrapping data for block:  DEONI
--//--//--//--//--Scrapping data for block:  JALKOT
--//--//--//--//--Scrapping data for block:  LATUR
--//--//--//--//--Scrapping data for block:  NILANGA
--//--//--//--//--Scrapping data for block:  RENAPUR
--//--//--//--//--Scrapping data for block:  SHIRUR ANANTPAL
--//--//--//--//--Scrapping data for block:  UDGIR
--//--//--//--Scrapping data for district:  NAGPUR
--//--//--//--//--Scrapping data for block:  BHIWAPUR
--//--/

--//--//--//--Scrapping data for district:  AGAR-MALWA
--//--//--//--Scrapping data for district:  ALIRAJPUR
--//--//--//--Scrapping data for district:  ANUPPUR
--//--//--//--Scrapping data for district:  ASHOK NAGAR
--//--//--//--Scrapping data for district:  BALAGHAT
--//--//--//--Scrapping data for district:  BARWANI
--//--//--//--Scrapping data for district:  BETUL
--//--//--//--Scrapping data for district:  BHIND
--//--//--//--Scrapping data for district:  BHOPAL
--//--//--//--Scrapping data for district:  BURHANPUR
--//--//--//--Scrapping data for district:  CHHATARPUR
--//--//--//--Scrapping data for district:  CHHINDWARA
--//--//--//--Scrapping data for district:  DAMOH
--//--//--//--Scrapping data for district:  DATIA
--//--//--//--Scrapping data for district:  DEWAS
--//--//--//--Scrapping data for district:  DHAR
--//--//--//--//--Scrapping data for block:  BADNAWAR
--//--//--//--//--Scrapping data for block:  BAGH
--//--//--//--//--Scrapping data for block:  DAHI
--//--//--

--//--//--//--Scrapping data for district:  AGAR-MALWA
--//--//--//--Scrapping data for district:  ALIRAJPUR
--//--//--//--Scrapping data for district:  ANUPPUR
--//--//--//--Scrapping data for district:  ASHOK NAGAR
--//--//--//--Scrapping data for district:  BALAGHAT
--//--//--//--Scrapping data for district:  BARWANI
--//--//--//--Scrapping data for district:  BETUL
--//--//--//--Scrapping data for district:  BHIND
--//--//--//--Scrapping data for district:  BHOPAL
--//--//--//--Scrapping data for district:  BURHANPUR
--//--//--//--Scrapping data for district:  CHHATARPUR
--//--//--//--Scrapping data for district:  CHHINDWARA
--//--//--//--//--Scrapping data for block:  AMARWARA
--//--//--//--//--Scrapping data for block:  BICHHUA
--//--//--//--//--Scrapping data for block:  CHAURAI
--//--//--//--//--Scrapping data for block:  CHHINDWARA
--//--//--//--//--Scrapping data for block:  HARAI
--//--//--//--//--Scrapping data for block:  JAMAI
--//--//--//--//--Scrapping data for block:  

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--Scrapping data for state:  PUNJAB
--//--//--Scrapping data for state:  RAJASTHAN
--//--//--Scrapping data for state:  SIKKIM
--//--//--Scrap

--//--//--//--//--Scrapping data for block:  AMBEGAON
--//--//--//--//--Scrapping data for block:  BARAMATI
--//--//--//--//--Scrapping data for block:  BHOR
--//--//--//--//--Scrapping data for block:  DAUND
--//--//--//--//--Scrapping data for block:  HAVELI
--//--//--//--//--Scrapping data for block:  INDAPUR
--//--//--//--//--Scrapping data for block:  JUNNAR
--//--//--//--//--Scrapping data for block:  KHED
--//--//--//--//--Scrapping data for block:  MAWAL
--//--//--//--//--Scrapping data for block:  MULSHI
--//--//--//--//--Scrapping data for block:  PUNE CITY
--//--//--//--//--Scrapping data for block:  PURANDHAR
--//--//--//--//--Scrapping data for block:  SHIRUR
--//--//--//--//--Scrapping data for block:  VELHE
--//--//--//--Scrapping data for district:  RAIGAD
--//--//--//--Scrapping data for district:  RATNAGIRI
--//--//--//--//--Scrapping data for block:  CHIPLUN
--//--//--//--//--Scrapping data for block:  DAPOLI
--//--//--//--//--Scrapping data for block:  GUHAGAR
--//-

In [17]:
df = pd.concat(df_list)

In [18]:
df

#SNo    Panchayat Name  Houses completed for prior to 2011-2012  \
1    1.0         ADHOMAJRA                                        0   
2    2.0             AHEMA                                        0   
3    3.0            AMIPUR                                        0   
4    4.0   ANANDPURJALBERA                                        0   
5    5.0          BABAHERI                                        0   
6    6.0           BAKNAUR                                        0   
7    7.0            BALANA                                        0   
8    8.0           BALAPUR                                        0   
9    9.0           BAROULA                                        0   
10  10.0           BAROULI                                        0   
11  11.0             BARRA                                        0   
12  12.0          BATROHAN                                        0   
13  13.0        BEGO MAJRA                                        0   
14  14.0         BEHBALPUR                                        0   
15  15.0        BHANOKHERI                                        0   
16  16.0  BHANPUR NAKATPUR                                        0   
17  17.0             BHARI                                        0   
18  18.0            BHERSA                                        0   
19  19.0            BHUNNI                                        0   
20  20.0        BHURANGPUR                                        0   
21  21.0       BHURE MAJRA                                        0   
22  22.0        BISHANGARH                                        0   
23  23.0           CHHAPRA                                        0   
24  24.0    CHHOTA BAROULA                                        0   
25  25.0         DANGERIAN                                        0   
26  26.0           DANIPUR                                        0   
27  27.0         DELUMAJRA                                        0   
28  28.0           DEVDPUR                                        0   
29  29.0          DHANOURA                                        0   
30  30.0          DHANOURI                                        0   
..   ...               ...                                      ...   
48  48.0           KHOLLHD                                        0   
49  49.0            KITOLI                                        0   
50  50.0             KOTMA                                        0   
51  51.0        LAKHBARIYA                                        0   
52  52.0            LALPUR                                        0   
53  53.0       MACHIGHANWA                                        0   
54  54.0             MADWA                                        0   
55  55.0             MAIKI                                        0   
56  56.0          MITHOURI                                        0   
57  57.0          NABALPUR                                        0   
58  58.0             NARGI                                        0   
59  59.0            NARWAR                                        0   
60  60.0         PACHAGAON                                        0   
61  61.0   PADMANIYA KHURD                                        0   
62  62.0     PADMNIYAKALAN                                        0   
63  63.0           PATAKAI                                        0   
64  64.0            PATARA                                        0   
65  65.0            PATASI                                        0   
66  66.0          PIPARIYA                                        0   
67  67.0            PONGRI                                        0   
68  68.0          SAMATPUR                                        0   
69  69.0        SARAIKANPA                                        0   
70  70.0         SARANGPUR                                        0   
71  71.0   SENDURI CHUNIYA                                        0   
72  72.0      SENDURIBARRY  

In [19]:
#merge all dataframes to master dataframe
df = pd.concat(df_list)
df = df.reset_index().drop(columns=['index', '#SNo'])
df['#SNo'] = df.index + 1
#Save Scrapped File
df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)